In [ ]:
# ..... merge metacells within each stage ..... #

In [2]:
library(igraph)

In [17]:
currstage = 'stage32'
mergedf = read.delim(paste0(currstage, '_merge_metacell_de.csv'), sep = ',')
mergedf[1,]

cell1 cell2 merge
1 1     160   0

In [18]:
dim(mergedf)
mergedf2 <- mergedf[mergedf$merge==1,]
dim(mergedf2)

[1] 21528     3

[1] 688   3

In [19]:
# metacell connectivity matrix
celltypes = sort(unique(c(unlist(mergedf$cell1), unlist(mergedf$cell2))))
cmat = matrix(0, nrow = length(celltypes), ncol = length(celltypes))
for(ii in 1:dim(mergedf2)[1]){
    c1 = match(mergedf2[ii,1], celltypes)
    c2 = match(mergedf2[ii,2], celltypes)
    cmat[c1,c2] = 1
    cmat[c2,c1] = 1
}
rownames(cmat) <- celltypes
colnames(cmat) <- celltypes

In [20]:
# get all possible connected nodes using igraph shortest_paths()
cmat2 <- shortest.paths(graph_from_adjacency_matrix(cmat))
cmat2[4:6,4:6]

4 5 6
4 0 1 1
5 1 0 1
6 1 1 0

In [21]:
# get list of matched celltypes
celltypes2 = celltypes
list1 = data.frame(cluster = paste0('cluster_', 1:length(celltypes)), 
                   elements = NA, num_elements = NA)
pb = txtProgressBar(min = 0, max = length(celltypes), initial = 0)
ctr = 1
df1 = c()

for(ii in 1:length(celltypes)){
    if(length(celltypes2)){
        ctype = celltypes2[1]
        ctype2 = c(ctype, names(which(cmat2[ctype,]!=Inf & cmat2[ctype,]>0)))
        list1$elements[ii] = paste(ctype2, collapse = ', ')
        list1$num_elements[ii] = length(ctype2)        
        celltypes2 <- setdiff(celltypes2, ctype2)
        
        # make full df
        temp = data.frame(cluster = rep(paste0('cluster_', ctr), length(ctype2)),
                                        metacell = ctype2)
        df1 = rbind(df1, temp)
        ctr = ctr + 1
    }
    setTxtProgressBar(pb, ii)
}
list1 <- list1[!is.na(list1$elements),]
length(celltypes)
dim(list1)
head(list1)

[1] 208

[1] 64  3

cluster  
1 cluster_1
2 cluster_2
3 cluster_3
4 cluster_4
5 cluster_5
6 cluster_6
  elements                                                                                      
1 1                                                                                             
2 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 39
3 27, 28, 29, 30, 31, 32, 33                                                                    
4 34                                                                                            
5 35                                                                                            
6 36, 37                                                                                        
  num_elements
1  1          
2 26          
3  7          
4  1          
5  1          
6  2

In [22]:
df1[1:2,]

cluster   metacell
1 cluster_1 1       
2 cluster_2 2

In [23]:
write.table(df1, file = paste0(currstage, '_cluster_from_metacell_de.csv'),
            sep = ',', row.names = F, col.names = T, quote = F)